In [276]:
import pandas as pd
import numpy as np
import seaborn as sns
import regex, re, sys, nltk
import nltk
import string
import geonamescache 
gc = geonamescache.GeonamesCache()
from nltk import word_tokenize, sent_tokenize
from nltk.tokenize import RegexpTokenizer
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords, wordnet

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import LatentDirichletAllocation

from wordcloud import WordCloud
from collections import Counter
from pathlib import Path
src_path = str(Path.cwd())

In [230]:
filepath = Path.cwd() / "WELFake_Dataset.csv"
df = pd.read_csv(filepath)
df.dtypes

Unnamed: 0     int64
title         object
text          object
label          int64
dtype: object

In [231]:
#Remove NaN in column text
df['check']=df[['text']].applymap(np.isreal)
df=df.loc[df['check']==False]
df.drop('check',axis=1,inplace=True)

In [233]:
# Apply lower case to avoid case sensitiviness
df['text']=df['text'].str.lower()
#select Reuters news 
df =  df[df['text'].str.contains("(reuters)")]
# Remove stopwords
STOPWORDS = set(stopwords.words('english'))
def remove_stopwords(text):
    """custom function to remove the stopwords"""
    return " ".join([word for word in str(text).split() if word not in STOPWORDS])

df['wo_stop'] = df['text'].apply(lambda text: remove_stopwords(text))
#Remove punctuation
PUNCT_TO_REMOVE = string.punctuation
def remove_punctuation(text):
    """custom function to remove the punctuation"""
    return text.translate(str.maketrans('', '', PUNCT_TO_REMOVE))

df["wo_punct"] = df["wo_stop"].apply(lambda text: remove_punctuation(text))
df.head()

C:\Users\aleja\AppData\Local\Temp/ipykernel_20780/774522822.py:4: UserWarning: This pattern has match groups. To actually get the groups, use str.extract.
  df =  df[df['text'].str.contains("(reuters)")]


Unnamed: 0                                              title  \
11          11  May Brexit offer would hurt, cost EU citizens ...   
12          12  Schumer calls on Trump to appoint official to ...   
15          15  Billionaire Odebrecht in Brazil scandal releas...   
17          17  U.N. seeks humanitarian pause in Sanaa where s...   
19          19  Second judge says Clinton email setup may have...   

                                                 text  label  \
11  brussels (reuters) - british prime minister th...      0   
12  washington (reuters) - charles schumer, the to...      0   
15  rio de janeiro/sao paulo (reuters) - billionai...      0   
17  geneva (reuters) - the united nations called o...      0   
19  new york (reuters) - a second federal judge ha...      0   

                                              wo_stop  \
11  brussels (reuters) - british prime minister th...   
12  washington (reuters) - charles schumer, top de...   
15  rio de janeiro/sao paulo (reuters) - billionai...   
17  geneva (reuters) - united nations called monda...   
19  new york (reuters) - second federal judge take...   

                                             wo_punct  
11  brussels reuters  british prime minister there...  
12  washington reuters  charles schumer top democr...  
15  rio de janeirosao paulo reuters  billionaire m...  
17  geneva reuters  united nations called monday h...  
19  new york reuters  second federal judge taken r...

In [241]:
#Lemmatizer
lemmatizer = WordNetLemmatizer()
wordnet_map = {"N":wordnet.NOUN, "V":wordnet.VERB, "J":wordnet.ADJ, "R":wordnet.ADV}
def lemmatize_words(text):
    pos_tagged = nltk.pos_tag(text.split())
    return " ".join([lemmatizer.lemmatize(word, wordnet_map.get(pos[0], wordnet.NOUN)) for word, pos in pos_tagged])

df["lemmatized"] = df["wo_punct"].apply(lambda text: lemmatize_words(text))


Unnamed: 0                                              title  \
11             11  May Brexit offer would hurt, cost EU citizens ...   
12             12  Schumer calls on Trump to appoint official to ...   
15             15  Billionaire Odebrecht in Brazil scandal releas...   
17             17  U.N. seeks humanitarian pause in Sanaa where s...   
19             19  Second judge says Clinton email setup may have...   
...           ...                                                ...   
72112       72112  United States and Cuba complete deals as Trump...   
72120       72120  North Korea's Kim congratulates China's Xi aft...   
72122       72122  Swiss stop seizing income from asylum seekers ...   
72129       72129  Russians steal research on Trump in hack of U....   
72132       72132  Trump tussle gives unpopular Mexican leader mu...   

                                                    text  label  \
11     brussels (reuters) - british prime minister th...      0   
12     washington (reuters) - charles schumer, the to...      0   
15     rio de janeiro/sao paulo (reuters) - billionai...      0   
17     geneva (reuters) - the united nations called o...      0   
19     new york (reuters) - a second federal judge ha...      0   
...                                                  ...    ...   
72112  havana (reuters) - the obama administration an...      0   
72120  seoul (reuters) - north korean leader kim jong...      0   
72122  zurich (reuters) - switzerland will stop seizi...      0   
72129  washington (reuters) - hackers believed to be ...      0   
72132  mexico city (reuters) - donald trump’s combati...      0   

                                                 wo_stop  \
11     brussels (reuters) - british prime minister th...   
12     washington (reuters) - charles schumer, top de...   
15     rio de janeiro/sao paulo (reuters) - billionai...   
17     geneva (reuters) - united nations called monda...   
19     new york (reuters) - second federal judge take...   
...                                                  ...   
72112  havana (reuters) - obama administration cuba c...   
72120  seoul (reuters) - north korean leader kim jong...   
72122  zurich (reuters) - switzerland stop seizing in...   
72129  washington (reuters) - hackers believed workin...   
72132  mexico city (reuters) - donald trump’s combati...   

                                                wo_punct  \
11     brussels reuters  british prime minister there...   
12     washington reuters  charles schumer top democr...   
15     rio de janeirosao paulo reuters  billionaire m...   
17     geneva reuters  united nations called monday h...   
19     new york reuters  second federal judge taken r...   
...                                                  ...   
72112  havana reuters  obama administration cuba cont...   
72120  seoul reuters  north korean leader kim jong un...   
72122  zurich reuters  switzerland stop seizing incom...   
72129  washington reuters  hackers believed working r...   
72132  mexico city reuters  donald trump’s combative ...   

                                              lemmatized  \
11     brussels reuters british prime minister theres...   
12     washington reuters charles schumer top democra...   
15     rio de janeirosao paulo reuters billionaire ma...   
17     geneva reuters unite nation call monday humani...   
19     new york reuters second federal judge take rar...   
...                                                  ...   
72112  havana reuters obama administration cuba conti...   
72120  seoul reuters north korean leader kim jong un ...   
72122  zurich reuters switzerland stop seize income w...   
72129  washington reuters hacker believe work russian...   
72132  mexico city reuters donald trump’s combative s...   

                                               tokenized    location  
11     [brussels, reuters, british, prime, minister, ...    brussels  
12     [washington, reuters, cha

In [308]:
for idx in cities:
    for idk,name in cities[idx].items():
        print(name)

3041563
Andorra la Vella
42.50779
1.52109
AD
20430
Europe/Andorra
07
['ALV', 'Ando-la-Vyey', 'Andora', 'Andora la Vela', 'Andora la Velja', "Andora lja Vehl'ja", 'Andoro Malnova', 'Andorra', 'Andorra Tuan', 'Andorra a Vella', 'Andorra la Biella', 'Andorra la Vella', 'Andorra la Vielha', 'Andorra-a-Velha', "Andorra-la-Vel'ja", 'Andorra-la-Vielye', 'Andorre-la-Vieille', 'Andò-la-Vyèy', 'Andòrra la Vièlha', 'an dao er cheng', 'andolalabeya', 'andwra la fyla', 'Ανδόρρα', 'Андора ла Веля', 'Андора ла Веља', 'Андора ля Вэлья', 'Андорра-ла-Велья', 'אנדורה לה וולה', 'أندورا لا فيلا', 'አንዶራ ላ ቬላ', 'アンドラ・ラ・ヴェリャ', '安道爾城', '안도라라베야']
290594
Umm Al Quwain City
25.56473
55.55517
AE
62747
Asia/Dubai
07
['Oumm al Qaiwain', 'Oumm al Qaïwaïn', 'Um al Kawain', 'Um al Quweim', 'Umm Al Quwain City', 'Umm al Qaiwain', 'Umm al Qawain', 'Umm al Qaywayn', 'Umm al-Quwain', "Umm-ehl'-Kajvajn", 'Yumul al Quwain', 'am alqywyn', 'mdynt am alqywyn', 'Умм-эль-Кайвайн', 'أم القيوين', 'مدينة ام القيوين']
291074
Ras Al K

-12.38333
16.93333
AO
113624
Africa/Luanda
02
['Bie', 'Bihe', 'Bihé', 'Bié', 'Cuito', 'Cuíto', 'Kuito', 'SVP', 'Silva Porto', 'Vila Salva Porto', 'Куито']
3348313
Huambo
-12.77611
15.73917
AO
226145
Africa/Luanda
08
['Huambas', 'Huambo', 'Huamdo', 'Khuambo', 'NOV', 'Nova Lisboa', 'Uambo', "hu'ambo", 'hwambw  angwla', 'uambu', 'uanbo', 'wambu', 'wan bo', 'Вилояти Ҳвамбо', 'Уамбо', 'Хуамбо', 'הואמבו', 'هوامبو، آنگولا', 'ہوامبو', 'ਹੁਆਂਬੋ', 'วัมบู', 'ウアンボ', '万博', '우암부']
3350246
Catumbela
-12.43002
13.54677
AO
16977
Africa/Luanda
01
['Asseiceira', 'CBT', 'Catumbela', 'Catumbella', 'Katumbela', 'Катумбела']
3350372
Catabola
-12.15
17.28333
AO
18855
Africa/Luanda
02
['Catabola', 'Katabola', 'Катабола']
3351014
Camacupa
-12.01667
17.48333
AO
19150
Africa/Luanda
02
['Camacupa', 'General Machado', 'General Machado Villa', 'General Mathado', 'Kamakupa', 'Machado', 'Vila General Machado', 'Камакупа']
3351500
Caála
-12.8525
15.56056
AO
21205
Africa/Luanda
08
['Caala', 'Cahala', 'Caála', 'Kaala', 'K

21
['Perez', 'Pérez']
3841956
Paraná
-31.73271
-60.52897
AR
262295
America/Argentina/Cordoba
08
['Cittae de Parana', 'PRA', 'Parana', 'Paranà', 'Paraná', 'ba la na', 'barana  antry ryws', 'palana', 'parana', 'prnh', 'Çittæ de Paraná', 'Παρανά', 'Парана', 'Պարանա', 'פרנה', 'بارانا، انتري ريوس', 'پارانا', 'پارانا، انترے ریوس', 'პარანა', 'パラナ', '巴拉那', '파라나']
3842190
Palpalá
-24.25647
-65.21163
AR
48199
America/Argentina/Jujuy
10
['Palpala', 'Palpalá']
3842670
Olavarría
-36.89272
-60.32254
AR
86320
America/Argentina/Buenos_Aires
01
['OVR', 'Olavarija', 'Olavarria', 'Olavarrija', 'Olavarría', 'ao la wa li ya', 'awlafarya', 'awlawarya', 'olavaria', 'xo la bar ri xa', 'Олаварија', 'Олаваррия', 'أولافاريا', 'اولاواریا', 'โอลาบาร์รีอา', 'ოლავარია', '奧拉瓦里亞']
3842881
Nueve de Julio
-35.44437
-60.88313
AR
34718
America/Argentina/Buenos_Aires
01
['9 de Julio', 'Nev-de-Khulio', 'Nueve de Julio', 'Нев-де-Хулио']
3843123
Neuquén
-38.95161
-68.0591
AR
242092
America/Argentina/Salta
15
['Ciuda de Neuque

48.20849
16.37208
AT
1691468
Europe/Vienna
09
['Bec', 'Bech', 'Becs', 'Beç', 'Beč', 'Bienne', 'Bécs', 'Dunaj', 'VIE', 'Vena', 'Viden', "Viden'", 'Vieden', 'Viedeň', 'Viena', 'Vienna', 'Vienne', 'Vieno', 'Viin', 'Vin', 'Vinarborg', 'Vindobona', 'Viyana', 'Vídeň', 'Vín', 'Vínarborg', 'Wenen', 'Wieden', 'Wiedeń', 'Wien', 'bienna', 'bin', 'fyyna', 'weiynna', 'Βιέννη', 'Беч', 'Вена', 'Виена', 'Відень', 'فيينا', 'เวียนนา', 'ቪየና', '비엔나', '빈']
2761436
Wetzelsdorf
47.05293
15.39923
AT
15687
Europe/Vienna
06
['Wetzelsdorf']
2761524
Wels
48.16667
14.03333
AT
16857
Europe/Vienna
04
['Ovilava', "Vel's", 'Wels', 'wls', 'Вельс', 'ולס']
2761669
Weinzierl bei Krems
48.4
15.6
AT
24092
Europe/Vienna
03
['Weinzierl', 'Weinzierl bei Krems']
2762372
Villach
46.61028
13.85583
AT
58882
Europe/Vienna
02
['Beljak', 'Filachas', 'Filakh', 'Fillach', 'Fillaha', 'Fillakh', 'QVL', 'Santicum', 'Vilac', 'Villach', 'Villaco', 'fei la he', 'fil lakh', 'firahha', 'fylakh', 'pilakhi', 'pillaheu', 'pylʼk', 'wylakh', 'Φίλλα

AU
30921
Australia/Melbourne
07
['Noble Park']
2155472
Newcastle
-32.92953
151.7801
AU
308308
Australia/Sydney
02
["Avstralyn N'jukasl", "N'jukasl", 'NTL', 'Newcastle', 'Niukaslas', 'Njukasl', 'Njukasul', 'Novkastelo', "n'yukesala", 'niu ka si er', 'niyukacil', 'nyukaeseul', 'nyukassuru', 'nyw kasl', 'nywkasl', 'nywkasl  nyw sawt wlz', 'nywkasl  yyny gwnyy wlz', 'Њукасл', 'Австралын Ньюкасл', 'Ньюкасл', 'Нюкасъл', 'ניוקאסל', 'نيوكاسل', 'نیو کاسل', 'نیو کیسل، نیو ساؤتھ ویلز', 'نیوکاسل، نیو ساوت ولز', 'نیوکاسل، یئنی گونئی ولز', 'نیوکاسڵ', 'न्यूकॅसल', 'நியூகாசில்', 'ნიუკასლი', 'ニューカッスル', '纽卡斯尔', '뉴캐슬']
2155542
Nerang
-27.98941
153.33633
AU
16739
Australia/Brisbane
04
['Nerang']
2155718
Narre Warren
-38.03333
145.3
AU
26389
Australia/Melbourne
07
['']
2155787
Narangba
-27.20338
152.95923
AU
18217
Australia/Brisbane
04
['Narangba']
2156340
Mulgrave
-37.92845
145.17708
AU
17647
Australia/Melbourne
07
['Mulgrave']
2156492
Mount Waverley
-37.87709
145.12939
AU
33149
Australia/Melbourne
07
['Mo

...

68.16768
UZ
24856
Asia/Samarkand
15
['Erjar', 'Gagarin', 'Gagarin Shahri', 'Yerzhar', 'Гагарин']
1514019
Fergana
40.38421
71.78432
UZ
164322
Asia/Tashkent
03
['FEG', "Farg'ona", 'Farghana', 'Farghona', 'Farghāna', 'Fargona', 'Fargʻona', 'Fergan', 'Fergana', 'Fergano', 'Ferganá', 'Ferghana', 'Fernkana', 'Fərqanə', 'Novyy Margelan', 'Skobelev', 'Skobelevo', 'fei er gan na', 'ferugana', 'frghanh', 'frghanh\u200e', 'frghant', 'fyrghana', 'peleugana', 'prgnh', 'Φεργκάνα', 'Фарғона', 'Фергана', 'Ֆերգանա', 'פרגנה', 'فرغانة', 'فرغانه', 'فرغانه\u200e', 'فرغانہ', 'فیرغانا', 'فەرغانە', 'ഫെർഗാന', 'フェルガナ', '费尔干纳', '페르가나']
1514125
Do’stlik Shahri
40.52881
68.03153
UZ
16524
Asia/Samarkand
15
["Do'stlik", "Do'stlik Shahri", 'Do’stlik', 'Do’stlik Shahri', 'Dustlik', 'Dŭstlik']
1514192
Chust
41.00329
71.23791
UZ
64966
Asia/Tashkent
06
['Chust', 'Chust Shahri', 'Tschust', 'Чуст']
1514210
Chirchiq
41.46889
69.58222
UZ
167842
Asia/Tashkent
14
['Chirchik', 'Chirchiq', 'Circig', 'Circik', 'Circikas', 'Tchirt

23
['Lagunillas']
3637624
Lagunillas
8.50457
-71.3894
VE
28176
America/Caracas
14
['Lagunillas']
3637721
La Guaira
10.60156
-66.93293
VE
25259
America/Caracas
26
['LAG', 'La Guaira', 'La Guayra', 'La Gvaira', 'La-Guajra', 'la gua yi la', 'la gwayra', 'la-guaira', 'lagwaila', 'ra・guaira', 'Ла-Гуайра', 'لا گوایرا', 'ლა-გუაირა', 'ラ・グアイラ', '拉瓜伊拉', '라과이라']
3638371
La Concepción
10.61919
-71.83814
VE
78106
America/Caracas
23
['']
3638374
Concepción
10.4119
-71.68919
VE
40313
America/Caracas
23
['Concepcion', 'Concepción', 'La Concepcion', 'La Concepción']
3638904
La Azulita
8.71364
-71.44421
VE
17111
America/Caracas
14
['La Azulita']
3639086
Judibana
11.75054
-70.19355
VE
23182
America/Caracas
11
['Judibana', 'Judivana']
3639107
Juan Griego
11.08172
-63.96549
VE
28256
America/Caracas
17
['']
3639526
Higuerote
10.48287
-66.10096
VE
41364
America/Caracas
15
['HGE', 'Higuerote']
3639725
Güiria
10.57721
-62.29841
VE
40000
America/Caracas
19
['GUI', 'Guiria', 'Güiria']
3639747
Güigüe
10.08344
-67

33
['Tai nin', 'Tay Ninh', "Tehjnin'", 'Tei Nin', 'Tây Ninh', 'Vilojati Tej Nin', 'tainin', 'tay nynha', 'tteoinin', 'xi ning shi', 'Вилояти Тей Нин', 'Тэйнинь', 'Тэйнінь', 'تای نینها', 'تاے ننہ', 'タイニン', '西寧市', '떠이닌']
1567069
Tân An
10.53589
106.41366
VN
64801
Asia/Ho_Chi_Minh
24
['Tan', 'Tan Am', 'Tan An', 'Tân An', 'Тан']
1567148
Tam Kỳ
15.57364
108.47403
VN
59000
Asia/Ho_Chi_Minh
84
['Tam Ky', 'Tam Kỳ', 'Tanky']
1567621
Sơn Tây
21.14053
105.50686
VN
40636
Asia/Bangkok
44
['Son Tay', 'Son-Taj', 'Sontai', 'Sơn Tây', 'Сон-Тай']
1567681
Sơn La
21.3256
103.91882
VN
19054
Asia/Bangkok
32
['SQH', 'Son La', 'Son La Chau', 'Son Lu', 'Son-La', 'Sơn La', 'Thanh Pho Son La', 'Thành Phố Sơn La', 'shan luo shi', 'Сон-Ла', '山羅市']
1567723
Sông Cầu
13.4556
109.22348
VN
94066
Asia/Ho_Chi_Minh
61
['Bong Cau', 'Bông Cầu', 'Song Cau', 'Song Ka', 'Song Ko', 'Songkau', 'Sông Cầu']
1567788
Sóc Trăng
9.59995
105.97193
VN
114453
Asia/Ho_Chi_Minh
65
['Khanh Hong', 'Khanh Hung', 'Khánh Hưng', 'SOA', 'Shokchan

Vryheid
-27.76952
30.79165
ZA
150012
Africa/Johannesburg
02
['VYD', 'Vryheid']
942511
Vryburg
-26.95659
24.7284
ZA
49588
Africa/Johannesburg
10
['Frejburg', 'Frejburga', 'VRU', 'Vryburg', 'fu lei bao', 'Фрейбург', 'Фрейбурга', '弗雷堡']
943032
Volksrust
-27.36541
29.88175
ZA
43378
Africa/Johannesburg
07
['Volkrust', 'Volksrust']
943882
Virginia
-28.10391
26.86593
ZA
122502
Africa/Johannesburg
03
['Virdzhinija', 'Virginia', 'Вирджиния']
943960
Viljoenskroon
-27.20841
26.94855
ZA
54955
Africa/Johannesburg
03
['Viljoenskroon']
944385
Vereeniging
-26.67313
27.92615
ZA
474681
Africa/Johannesburg
06
['Feriniging', 'Ferinikhing', 'Vereeniging', 'Vereniging', 'Verenigingas', 'Verenigingo', 'ferinihingu', 'fu li ni xin', 'fyrynjngh', 'fyrynkhn', 'peleinihing', 'wrynygyng', 'Веренигинг', 'Феринихинг', 'Ферінігінг', 'فيرينجنغ', 'فيرينخن', 'ورینیگینگ', 'フェリーニヒング', '弗里尼欣', '페레이니힝']
944986
Vanderbijlpark
-26.71171
27.83795
ZA
246754
Africa/Johannesburg
06
['Fanderbajpark', 'Fanderbejlpark', 'Vanderbijl

Africa/Johannesburg
11
['Beaufort West', 'Beaufort-Wes', 'Bofort-Uehst', 'xi bo fu te', 'Бофорт-Уэст', 'بیوفورٹ غربی', '西博福特']
1021086
Barberton
-25.78842
31.05319
ZA
67927
Africa/Johannesburg
07
['Barberton', 'ba bo dun', '巴伯頓']
1021360
Ballito
-29.53897
31.21439
ZA
17218
Africa/Johannesburg
02
['Ballitoville']
1021396
Balfour
-26.66331
28.59016
ZA
46008
Africa/Johannesburg
07
["Bal'fur", 'Balfour', 'Бальфур']
1023287
Allanridge
-27.75431
26.64382
ZA
31700
Africa/Johannesburg
03
['Allanridge']
1023309
Aliwal North
-30.69366
26.71141
ZA
44436
Africa/Johannesburg
05
['Aliwal North', 'Aliwal-Noord', 'alywal shmal', 'bei a li wa er', 'آلیوال شمال', '北阿利瓦爾']
1023441
Alberton
-26.26786
28.12225
ZA
121536
Africa/Johannesburg
06
['Alberton']
1105726
Ekangala
-25.69619
28.74918
ZA
37650
Africa/Johannesburg
06
['Ekangala']
1105776
Midrand
-25.98953
28.12843
ZA
173009
Africa/Johannesburg
06
['Midrand', 'Мидранд']
1105777
Centurion
-25.85891
28.18577
ZA
233386
Africa/Johannesburg
06
['Centurion',

In [1]:
#save location and delete reuters
df['location']=df.lemmatized.apply(lambda x :x.split(' ', 1)[0])
#cities=gc.get_cities()
#df['location']=df.lemmatized.str.match(cities)
def cleaning(text):
    a=text.split(' ', 2)[2]
    return a.replace("reuters","")
    
df['clean']=df.lemmatized.apply(lambda x : cleaning(x))

df

NameError: name 'df' is not defined

In [271]:
# tokenize into sentences
tokenizer = RegexpTokenizer(r'\b(?!\d)[a-zA-Z]+')
df['tokenized']=df['clean'].apply((lambda text: tokenizer.tokenize(text)))
df

Unnamed: 0                                              title  \
11             11  May Brexit offer would hurt, cost EU citizens ...   
12             12  Schumer calls on Trump to appoint official to ...   
15             15  Billionaire Odebrecht in Brazil scandal releas...   
17             17  U.N. seeks humanitarian pause in Sanaa where s...   
19             19  Second judge says Clinton email setup may have...   
...           ...                                                ...   
72112       72112  United States and Cuba complete deals as Trump...   
72120       72120  North Korea's Kim congratulates China's Xi aft...   
72122       72122  Swiss stop seizing income from asylum seekers ...   
72129       72129  Russians steal research on Trump in hack of U....   
72132       72132  Trump tussle gives unpopular Mexican leader mu...   

                                                    text  label  \
11     brussels (reuters) - british prime minister th...      0   
12     washington (reuters) - charles schumer, the to...      0   
15     rio de janeiro/sao paulo (reuters) - billionai...      0   
17     geneva (reuters) - the united nations called o...      0   
19     new york (reuters) - a second federal judge ha...      0   
...                                                  ...    ...   
72112  havana (reuters) - the obama administration an...      0   
72120  seoul (reuters) - north korean leader kim jong...      0   
72122  zurich (reuters) - switzerland will stop seizi...      0   
72129  washington (reuters) - hackers believed to be ...      0   
72132  mexico city (reuters) - donald trump’s combati...      0   

                                                 wo_stop  \
11     brussels (reuters) - british prime minister th...   
12     washington (reuters) - charles schumer, top de...   
15     rio de janeiro/sao paulo (reuters) - billionai...   
17     geneva (reuters) - united nations called monda...   
19     new york (reuters) - second federal judge take...   
...                                                  ...   
72112  havana (reuters) - obama administration cuba c...   
72120  seoul (reuters) - north korean leader kim jong...   
72122  zurich (reuters) - switzerland stop seizing in...   
72129  washington (reuters) - hackers believed workin...   
72132  mexico city (reuters) - donald trump’s combati...   

                                                wo_punct  \
11     brussels reuters  british prime minister there...   
12     washington reuters  charles schumer top democr...   
15     rio de janeirosao paulo reuters  billionaire m...   
17     geneva reuters  united nations called monday h...   
19     new york reuters  second federal judge taken r...   
...                                                  ...   
72112  havana reuters  obama administration cuba cont...   
72120  seoul reuters  north korean leader kim jong un...   
72122  zurich reuters  switzerland stop seizing incom...   
72129  washington reuters  hackers believed working r...   
72132  mexico city reuters  donald trump’s combative ...   

                                              lemmatized  \
11     brussels reuters british prime minister theres...   
12     washington reuters charles schumer top democra...   
15     rio de janeirosao paulo reuters billionaire ma...   
17     geneva reuters unite nation call monday humani...   
19     new york reuters second federal judge take rar...   
...                                                  ...   
72112  havana reuters obama administration cuba conti...   
72120  seoul reuters north korean leader kim jong un ...   
72122  zurich reuters switzerland stop seize income w...   
72129  washington reuters hacker believe work russian...   
72132  mexico city reuters donald trump’s combative s...   

                                               tokenized    location  \
11     [british, prime, minister, theresa, may, offer...    brussels   
12     [charles, schumer, top,

In [272]:
df['len_art']= df['tokenized'].apply(lambda x: len(x))
df=df.loc[df['len_art']>300]
df

Unnamed: 0                                              title  \
27             27  Islamic State driven out of last stronghold in...   
33             33  Schaeuble to head German parliament, unblockin...   
34             34  At U.S.-China summit, Trump presses Xi on trad...   
47             47  Illinois House passes $5 billion tax package, ...   
51             51  Fear of Iranian general left Iraqi Kurdish oil...   
...           ...                                                ...   
72074       72074  Two Palestinians killed in anti-US protests af...   
72106       72106  'Gates of Hell': Iraqi army says fighting near...   
72120       72120  North Korea's Kim congratulates China's Xi aft...   
72129       72129  Russians steal research on Trump in hack of U....   
72132       72132  Trump tussle gives unpopular Mexican leader mu...   

                                                    text  label  \
27     baghdad (reuters) - iraqi forces announced on ...      0   
33     berlin (reuters) - germany took a first decisi...      0   
34     palm beach, fla. (reuters) - president donald ...      0   
47     chicago (reuters) - illinois’ democratic-contr...      0   
51     baghdad/london (reuters) - when the iraqi army...      0   
...                                                  ...    ...   
72074  gaza (reuters) - israeli troops shot dead at l...      0   
72106   (story corrects third paragraph to show mosul...      0   
72120  seoul (reuters) - north korean leader kim jong...      0   
72129  washington (reuters) - hackers believed to be ...      0   
72132  mexico city (reuters) - donald trump’s combati...      0   

                                                 wo_stop  \
27     baghdad (reuters) - iraqi forces announced thu...   
33     berlin (reuters) - germany took first decisive...   
34     palm beach, fla. (reuters) - president donald ...   
47     chicago (reuters) - illinois’ democratic-contr...   
51     baghdad/london (reuters) - iraqi army iranian-...   
...                                                  ...   
72074  gaza (reuters) - israeli troops shot dead leas...   
72106  (story corrects third paragraph show mosul fel...   
72120  seoul (reuters) - north korean leader kim jong...   
72129  washington (reuters) - hackers believed workin...   
72132  mexico city (reuters) - donald trump’s combati...   

                                                wo_punct  \
27     baghdad reuters  iraqi forces announced thursd...   
33     berlin reuters  germany took first decisive st...   
34     palm beach fla reuters  president donald trump...   
47     chicago reuters  illinois’ democraticcontrolle...   
51     baghdadlondon reuters  iraqi army iranianbacke...   
...                                                  ...   
72074  gaza reuters  israeli troops shot dead least t...   
72106  story corrects third paragraph show mosul fell...   
72120  seoul reuters  north korean leader kim jong un...   
72129  washington reuters  hackers believed working r...   
72132  mexico city reuters  donald trump’s combative ...   

                                              lemmatized  \
27     baghdad reuters iraqi force announce thursday ...   
33     berlin reuters germany take first decisive ste...   
34     palm beach fla reuters president donald trump ...   
47     chicago reuters illinois’ democraticcontrolled...   
51     baghdadlondon reuters iraqi army iranianbacked...   
...                                                  ...   
72074  gaza reuters israeli troop shoot dead least tw...   
72106  story corrects third paragraph show mosul fell...   
72120  seoul reuters north korean leader kim jong un ...   
72129  washington reuters hacker believe work russian...   
72132  mexico city reuters donald trump’s combative s...   

                                               tokenized       location  \
27     [iraqi, force, announce, thursday, capture, is...        baghdad   
33     [germany, take, f

In [273]:
lda = LatentDirichletAllocation(n_components=10,random_state=0) # 25
tf_vectorizer = CountVectorizer(stop_words='english', ngram_range=(1, 2), max_features=2000)
tf_matrix = tf_vectorizer.fit_transform(df['clean'])
tf_feature_names = tf_vectorizer.get_feature_names()  #get_feature_names_out() doesn't work anymore
tf_df = pd.DataFrame(tf_matrix.toarray(), columns = tf_feature_names)
tf_df

10  100  11  12  13  14  15  16  17  18  ...  xi jinping  year  \
0      0    0   0   0   0   0   0   0   0   0  ...           0     0   
1      0    0   0   0   0   0   1   0   0   0  ...           0     2   
2      0    1   0   0   0   0   0   0   0   0  ...           1     1   
3      0    0   0   0   0   0   3   0   0   0  ...           0     4   
4      0    0   0   1   0   0   0   0   1   0  ...           0     0   
...   ..  ...  ..  ..  ..  ..  ..  ..  ..  ..  ...         ...   ...   
6131   1    0   0   0   0   0   0   0   0   0  ...           0     0   
6132   0    0   1   0   0   0   0   0   0   0  ...           0     0   
6133   0    0   0   0   0   0   0   0   0   0  ...           1     1   
6134   0    0   0   0   0   0   0   0   0   0  ...           0     2   
6135   0    0   0   0   0   0   0   0   0   0  ...           0     2   

      year ago  yemen  yes  york  york time  young  zika  zone  
0            0      0    0     0          0      0     0     0  
1            0      0    0     0          0      0     0     6  
2            0      0    0     0          0      0     0     0  
3            1      0    1     0          0      0     0     0  
4            0      0    0     0          0      0     0     0  
...        ...    ...  ...   ...        ...    ...   ...   ...  
6131         0      0    0     0          0      0     0     0  
6132         0      0    0     0          0      0     0     0  
6133         0      0    0     0          0      0     0     0  
6134         0      0    0     0          0      0     0     0  
6135         0      0    0     0          0      0     0     0  

[6136 rows x 2000 columns]